## Stable Diffusion

In [9]:
! python -m pip install --upgrade pip
! pip install botocore --upgrade --quiet

Looking in indexes: https://pypi.org/simple, https://pip.repos.neuron.amazonaws.com, https://pypi.ngc.nvidia.com
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 37.6 MB/s eta 0:00:00a 0:00:01
  Attempting uninstall: pip
    Found existing installation: pip 22.3.1
    Uninstalling pip-22.3.1:
      Successfully uninstalled pip-22.3.1
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
awscli 1.27.71 requires botocore==1.29.71, but you have botocore 1.29.105 which is incompatible.


In [10]:
!pip list|grep -i diffuser

diffusers                     0.14.0


In [11]:
!pip install "sagemaker==2.116.0" "huggingface_hub==0.13.1" --upgrade --quiet

In [12]:
import sagemaker
import boto3
sess = sagemaker.Session()
# sagemaker session bucket -> used for uploading data, models and logs
# sagemaker will automatically create this bucket if it not exists
sagemaker_session_bucket=None
if sagemaker_session_bucket is None and sess is not None:
    # set to default bucket if a bucket name is not given
    sagemaker_session_bucket = sess.default_bucket()

try:
    role = sagemaker.get_execution_role()
except ValueError:
    iam = boto3.client('iam')
    role = iam.get_role(RoleName='sagemaker_execution_role')['Role']['Arn']

sess = sagemaker.Session(default_bucket=sagemaker_session_bucket)

print(f"sagemaker role arn: {role}")
print(f"sagemaker bucket: {sess.default_bucket()}")
print(f"sagemaker session region: {sess.boto_region_name}")

sagemaker role arn: arn:aws:iam::687912291502:role/sm-fs-streaming-agg-stack-SageMakerRole-PLMML6TNNEV2
sagemaker bucket: sagemaker-us-west-2-687912291502
sagemaker session region: us-west-2


In [14]:
#!pip install torch==1.12.1+cu113 torchvision==0.13.1+cu113 --extra-index-url https://download.pytorch.org/whl/cu113
!pip install -r ./requirements.txt
!torch_version=1.13.1
!pip3 install torch==1.13.1+cu117 --extra-index-url https://download.pytorch.org/whl/cu117
!pip3 install bitsandbytes

Looking in indexes: https://pypi.org/simple, https://pip.repos.neuron.amazonaws.com, https://pypi.ngc.nvidia.com
Looking in indexes: https://pypi.org/simple, https://pip.repos.neuron.amazonaws.com, https://pypi.ngc.nvidia.com, https://download.pytorch.org/whl/cu117
Looking in indexes: https://pypi.org/simple, https://pip.repos.neuron.amazonaws.com, https://pypi.ngc.nvidia.com


In [26]:
import os
import json
from diffusers import StableDiffusionPipeline
from diffusers import StableDiffusionImg2ImgPipeline
import boto3
import sagemaker
import uuid
import torch
from torch import autocast
from PIL import Image
import io
import requests
import traceback
import os
import json
import torch
from diffusers import StableDiffusionPipeline
from diffusers import StableDiffusionImg2ImgPipeline
from diffusers import StableDiffusionPipeline, DPMSolverMultistepScheduler
import deepspeed



#model_dir='/root/dreambooth/models_diffuser/'
model_dir='runwayml/stable-diffusion-v1-5'
#model_dir='andite/anything-v4.0'
#model_dir='/home/ec2-user/SageMaker/dst/'
pipeline = StableDiffusionPipeline.from_pretrained(model_dir, torch_dtype=torch.float16, revision="fp16")
#pipeline = StableDiffusionPipeline.from_pretrained(model_dir, torch_dtype=torch.float16, revision="fp16")
print("model loaded:",pipeline)
 
torch.backends.cudnn.benchmark = True
torch.backends.cuda.matmul.allow_tf32 = True


#try:
#   print("begin load deepspeed....")    
#   deepspeed.init_distributed()
#   engine = deepspeed.init_inference(
#       model=getattr(pipeline,"model", pipeline),      # Transformers models
#       mp_size=1,        # Number of GPU
#       dtype=torch.float16, # dtype of the weights (fp16)
#       replace_method="auto", # Lets DS autmatically identify the layer to replace
#       replace_with_kernel_inject=False, # replace the model with the kernel injector
#   )
##
#   if hasattr(pipeline, "model"):
#       pipeline.model = engine
#
#   print('model accelarate with deepspeed!')
#except Exception as e:
#   print("deepspeed accelarate excpetion!")
#   print(e)
    
pipeline = pipeline.to("cuda")
pipeline.enable_attention_slicing()    

Fetching 15 files:   0%|          | 0/15 [00:00<?, ?it/s]

/home/ec2-user/anaconda3/envs/pytorch_p39/lib/python3.9/site-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(
`text_config_dict` is provided which will be used to initialize `CLIPTextConfig`. The value `text_config["id2label"]` will be overriden.


model loaded: StableDiffusionPipeline {
  "_class_name": "StableDiffusionPipeline",
  "_diffusers_version": "0.14.0",
  "feature_extractor": [
    "transformers",
    "CLIPFeatureExtractor"
  ],
  "requires_safety_checker": true,
  "safety_checker": [
    "stable_diffusion",
    "StableDiffusionSafetyChecker"
  ],
  "scheduler": [
    "diffusers",
    "PNDMScheduler"
  ],
  "text_encoder": [
    "transformers",
    "CLIPTextModel"
  ],
  "tokenizer": [
    "transformers",
    "CLIPTokenizer"
  ],
  "unet": [
    "diffusers",
    "UNet2DConditionModel"
  ],
  "vae": [
    "diffusers",
    "AutoencoderKL"
  ]
}



### Inference

In [21]:
from PIL import Image
from io import BytesIO
from IPython.display import display
import base64
import matplotlib.pyplot as plt

# helper decoder
def decode_base64_image(image_string):
  base64_image = base64.b64decode(image_string)
  buffer = BytesIO(base64_image)
  return Image.open(buffer)

# display PIL images as grid
def display_images(images=None,columns=3, width=100, height=100):
    plt.figure(figsize=(width, height))
    for i, image in enumerate(images):
        plt.subplot(int(len(images) / columns + 1), columns, i + 1)
        plt.axis('off')
        plt.imshow(image)
        
def get_bucket_and_key(s3uri):
    pos = s3uri.find('/', 5)
    bucket = s3uri[5 : pos]
    key = s3uri[pos + 1 : ]
    return bucket, key        

In [27]:
%%time
import time
s3_client = boto3.client('s3')
#prompt = "A dog trying catch a flying pizza art drawn by disney concept artists, golden colour, high quality, highly detailed, elegant, sharp focus"
prompt = "portrait photo headshot by mucha, sharp focus, elegant, render, octane, detailed, award winning photography, masterpiece, rim lit"
#prompt = "priest, blue robes, 68 year old nun, national geographic, portrait, photo, photography"
#prompt = "hotel room with a swimming pool outside of the window, TV on the table, moon in the sky"

start=time.time()
images = pipeline(prompt, num_images_per_prompt=5, num_inference_steps=50, guidance_scale=9).images
print(f"Time taken: {time.time() - start}s")
ret_images=[]
for image in images:
   bucket, key = get_bucket_and_key("s3://sagemaker-us-west-2-687912291502/deepspeed/")
   key = '{0}{1}.jpg'.format(key, uuid.uuid4())
   buf = io.BytesIO()
   image.save(buf, format='JPEG')
   s3_client.put_object(
       Body = buf.getvalue(), 
       Bucket = bucket, 
       Key = key, 
       ContentType = 'image/jpeg'
   )
   ret_images.append(image)
   print('image: ', 's3://{0}/{1}'.format(bucket, key))



  0%|          | 0/50 [00:00<?, ?it/s]

Time taken: 18.959439992904663s
image:  s3://sagemaker-us-west-2-687912291502/deepspeed/42aa2e4a-0423-43c0-9884-3e24d6dc93a0.jpg
image:  s3://sagemaker-us-west-2-687912291502/deepspeed/c1b061ea-eb7e-4c09-b64c-68e42746c0e8.jpg
image:  s3://sagemaker-us-west-2-687912291502/deepspeed/53d615a0-254b-4bab-ae80-3a73b971a963.jpg
image:  s3://sagemaker-us-west-2-687912291502/deepspeed/b1bfdacc-b8a1-4e66-90d0-1ffc9f73e6d6.jpg
image:  s3://sagemaker-us-west-2-687912291502/deepspeed/60fdb5da-1786-4e0f-8377-b119066aab26.jpg
CPU times: user 15.5 s, sys: 3.58 s, total: 19.1 s
Wall time: 19.3 s


In [28]:
# visualize generation
display_images(ret_images)